In [ ]:

import pandas as pd
import numpy as np
import seaborn as sns
import datetime as dt
import matplotlib.pyplot as plt
import plotly.express as px





In [11]:
df = pd.read_csv("https://lead-program-assets.s3.eu-west-3.amazonaws.com/M05-Projects/fraudTest.csv")

df.head(3)

Unnamed: 0 trans_date_trans_time            cc_num  \
0           0   2020-06-21 12:14:25  2291163933867244   
1           1   2020-06-21 12:14:33  3573030041201292   
2           2   2020-06-21 12:14:53  3598215285024754   

                               merchant        category    amt   first  \
0                 fraud_Kirlin and Sons   personal_care   2.86    Jeff   
1                  fraud_Sporer-Keebler   personal_care  29.84  Joanne   
2  fraud_Swaniawski, Nitzsche and Welch  health_fitness  41.28  Ashley   

       last gender                street  ...      lat      long  city_pop  \
0   Elliott      M     351 Darlene Green  ...  33.9659  -80.9355    333497   
1  Williams      F      3638 Marsh Union  ...  40.3207 -110.4360       302   
2     Lopez      F  9333 Valentine Point  ...  40.6729  -73.5365     34496   

                      job         dob                         trans_num  \
0     Mechanical engineer  1968-03-19  2da90c7d74bd46a0caf3777415b3ebd3   
1  Sales professional, IT  1990-01-17  324cc204407e99f51b0d6ca0055005e7   
2       Librarian, public  1970-10-21  c81755dbbbea9d5c77f094348a7579be   

    unix_time  merch_lat  merch_long  is_fraud  
0  1371816865  33.986391  -81.200714         0  
1  1371816873  39.450498 -109.960431         0  
2  1371816893  40.495810  -74.196111         0  

[3 rows x 23 columns]

In [12]:
df.shape

(555719, 23)

Le jeu de données contient :
- 555 719 lignes
- 23 colonnes

In [13]:
print("\nPercentage of missing values: ")
display(100 * df.isnull().sum() / df.shape[0])


Percentage of missing values: 


Unnamed: 0               0.0
trans_date_trans_time    0.0
cc_num                   0.0
merchant                 0.0
category                 0.0
amt                      0.0
first                    0.0
last                     0.0
gender                   0.0
street                   0.0
city                     0.0
state                    0.0
zip                      0.0
lat                      0.0
long                     0.0
city_pop                 0.0
job                      0.0
dob                      0.0
trans_num                0.0
unix_time                0.0
merch_lat                0.0
merch_long               0.0
is_fraud                 0.0
dtype: float64

In [14]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 555719 entries, 0 to 555718
Data columns (total 23 columns):
 #   Column                 Non-Null Count   Dtype  
---  ------                 --------------   -----  
 0   Unnamed: 0             555719 non-null  int64  
 1   trans_date_trans_time  555719 non-null  object 
 2   cc_num                 555719 non-null  int64  
 3   merchant               555719 non-null  object 
 4   category               555719 non-null  object 
 5   amt                    555719 non-null  float64
 6   first                  555719 non-null  object 
 7   last                   555719 non-null  object 
 8   gender                 555719 non-null  object 
 9   street                 555719 non-null  object 
 10  city                   555719 non-null  object 
 11  state                  555719 non-null  object 
 12  zip                    555719 non-null  int64  
 13  lat                    555719 non-null  float64
 14  long                   555719 non-nu

In [18]:
nb_value = df.nunique()
print(df.nunique())

Unnamed: 0               555719
trans_date_trans_time    544760
cc_num                      924
merchant                    693
category                     14
amt                       37256
first                       341
last                        471
gender                        2
street                      924
city                        849
state                        50
zip                         912
lat                         910
long                        910
city_pop                    835
job                         478
dob                         910
trans_num                555719
unix_time                544760
merch_lat                546490
merch_long               551770
is_fraud                      2
dtype: int64


--> trans_num apparaît 555 719 fois : c’est l’index du jeu de données. <br>
--> La première colonne semble être un index du fichier et n’a aucune utilité fonctionnelle : cette colonne peut être supprimée.<br>
--> Intéret fonctionnel des données : <br>
les colonnes suivantes n'ont pas d'interet dans la détection de fraud :
- Unnamed: 0 → index artificiel → inutile
- cc_num → numéro carte → identifiant unique →  et non pertinent pour machine learning
- first, last → prénoms / noms → inutile (trop spécifique, pas généralisable)
- street, city, state, zip → adresse complète → inutile (trop spécifique et sensible)
- dob → date de naissance → inutile directement (pas pertinent)
- trans_num → ID transaction unique → inutile pas pertinents pour prédire la fraude.
- unix_time → doublon de la date → inutile (on garde uniquement les features dérivées)
- lat, long (client) et merch_lat, merch_long (commerçant) → données géographiques brutes, pas d'interet.
- job → trop de catégories (478 uniques), faible pouvoir explicatif → souvent supprimé <br>

Les données intéressantes:
- city_pop → population de la ville → peut être utile (corrélé à probabilité de fraude)
- trans_date_trans_time : à décliner en  hour + dayofweek
- merchant
- category
- gender
- amt : montant de la transaction

In [22]:
merchant =df['merchant'].unique()
merchant

array(['fraud_Kirlin and Sons', 'fraud_Sporer-Keebler',
       'fraud_Swaniawski, Nitzsche and Welch', 'fraud_Haley Group',
       'fraud_Johnston-Casper', 'fraud_Daugherty LLC',
       'fraud_Romaguera Ltd', 'fraud_Reichel LLC',
       'fraud_Goyette, Howell and Collier', 'fraud_Kilback Group',
       'fraud_Feil, Hilpert and Koss', 'fraud_Gottlieb Group',
       'fraud_Connelly-Carter', 'fraud_Bechtelar-Rippin',
       'fraud_Lubowitz-Walter', 'fraud_Welch, Rath and Koepp',
       'fraud_Hickle Group', 'fraud_Lang, Towne and Schuppe',
       'fraud_Morissette LLC', 'fraud_Prosacco LLC',
       'fraud_Corwin-Romaguera', 'fraud_Tillman LLC',
       'fraud_Veum-Koelpin', 'fraud_Watsica, Haag and Considine',
       'fraud_Leannon-Ward', 'fraud_Hintz, Bauch and Smith',
       'fraud_Labadie LLC', 'fraud_Eichmann, Hayes and Treutel',
       'fraud_Leffler-Goldner', 'fraud_Kautzer and Sons',
       'fraud_Ernser-Feest', 'fraud_Zemlak, Tillman and Cremin',
       'fraud_Nienow PLC', 'fraud_L

--> on remarque que tous les noms des commerçants sont préfixés par "fraud", on va pouvoir les supprimer ce prefixe pour ne garder que la valeur principale

In [19]:
# Format of gender
print (df['gender'].values)

['M' 'F' 'F' ... 'F' 'M' 'M']


--> La colonne du genre pourrait être mieux analysée comme une variable booléenne, avec {"M": 0, "F": 1}. <br>
--> Ainsi, les valeurs pourraient également être remappées.

In [ ]:
# Distribution of IsFraud


fig=px.pie(df, names='is_fraud')

fig.show()


--> le dataset est très déséquilibré : seulement 0.386% de ligne représente une fraude, soit 4 pour 1000 <br>
--> dans la classification, on va alors préférer le calcul du Recall pour la classe isFraud=1 (yes), <br>
>

PREPROCESSING A METTRE EN PLACE
1. Suppression de la colonne "Unnamed: 0"
2. mapping de la colone Gender
3. retirer le prefixe "fraud" dans la colonne merchant et en calculer un taux moyen
4. suppression des colonnes inutiles
4. metrique sur Recall et pas sur accuracy, pour mesurer au mieux les faux négatifs


